In [1]:
import logging

from neuralforecast import NeuralForecast

logging.getLogger('pytorch_lightning').setLevel(logging.ERROR)

USE_FARM = False

if USE_FARM:
    flag = "shaped"
else:
    flag = "raw"

In [7]:
from datasetsforecast.long_horizon2 import LongHorizon2
import pandas as pd

Y_df = LongHorizon2.load(directory='data', group='ETTh1')

target = "OT"
exog_list = ['HUFL', 'HULL', 'MUFL', 'MULL', "LUFL", "LULL"]

Y_df["ds"] = pd.to_datetime(Y_df["ds"])

Y_df = Y_df.set_index("ds")

df = Y_df[Y_df["unique_id"] == "OT"]
for item in Y_df["unique_id"].unique():
    if item == target:
        continue
    df[item] = Y_df[Y_df["unique_id"] == item]["y"]

df = df.reset_index()
Y_df = Y_df.reset_index()
df = df.drop("index", axis=1)
df

/tmp/ipykernel_3151/3190301915.py:17: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df[item] = Y_df[Y_df["unique_id"] == item]["y"]


ds unique_id         y      HUFL      HULL      MUFL  \
0     2016-07-01 00:00:00        OT  1.650715 -0.279827  0.052387 -0.508519   
1     2016-07-01 01:00:00        OT  1.322255 -0.301290  0.083769 -0.526247   
2     2016-07-01 02:00:00        OT  1.322255 -0.387142 -0.073140 -0.561537   
3     2016-07-01 03:00:00        OT  0.993915 -0.397873  0.021006 -0.561537   
4     2016-07-01 04:00:00        OT  0.623321 -0.354948  0.021006 -0.526247   
...                   ...       ...       ...       ...       ...       ...   
14395 2018-02-20 19:00:00        OT -2.003877  1.597691  0.428968  1.246043   
14396 2018-02-20 20:00:00        OT -2.003877  1.715737  0.554495  1.346115   
14397 2018-02-20 21:00:00        OT -1.776565  1.576229  0.397587  1.257807   
14398 2018-02-20 22:00:00        OT -1.742809  1.318674  0.272060  1.069262   
14399 2018-02-20 23:00:00        OT -1.726051  1.018355  0.146533  0.863320   

           MULL      LUFL      LULL  
0     -0.097223  1.046700  0.862183  
1     -0.115641  0.996503  0.908180  
2     -0.151967  0.696141  0.681165  
3     -0.133548  0.720828  0.771674  
4     -0.097223  0.771026  0.771674  
...         ...       ...       ...  
14395  0.248126  1.999628 -0.266953  
14396  0.339196  2.150220 -0.222440  
14397  0.302871  1.899233 -0.222440  
14398  0.211801  1.448279 -0.312949  
14399  0.175475  0.871420 -0.357462  

[14400 rows x 9 columns]

In [3]:
nf = NeuralForecast.load(path=f'./saved_models/etth1_{flag}_2025_04_11/')

Seed set to 7
Seed set to 16
/home/ubuntu/master_realm/lib/python3.12/site-packages/neuralforecast/common/_base_model.py:138: UserWarning: Input size too small. Automatically setting input size to 3 * horizon = 36
  warnings.warn(
/home/ubuntu/master_realm/lib/python3.12/site-packages/neuralforecast/common/_base_model.py:146: UserWarning: Inference input size too small. Automatically setting inference input size to input_size = 36
  warnings.warn(
Seed set to 5
/home/ubuntu/master_realm/lib/python3.12/site-packages/neuralforecast/models/lstm.py:161: UserWarning: context_size is deprecated and will be removed in future versions.
  warnings.warn(
/home/ubuntu/master_realm/lib/python3.12/site-packages/torch/storage.py:414: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.co

In [4]:
Y_hat_df = nf.predict()

GPU available: True (cuda), used: True
TPU available: False, using: 0 TPU cores
HPU available: False, using: 0 HPUs
You are using a CUDA device ('NVIDIA L4') that has Tensor Cores. To properly utilize them, you should set `torch.set_float32_matmul_precision('medium' | 'high')` which will trade-off precision for performance. For more details, read https://pytorch.org/docs/stable/generated/torch.set_float32_matmul_precision.html#torch.set_float32_matmul_precision
2025-04-11 17:39:25.206786: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:485] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
2025-04-11 17:39:25.219886: E external/local_xla/xla/stream_executor/cuda/cuda_dnn.cc:8454] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
2025-04-11 17:39:25.223903: E external/local_xla/xla/stream_executor/cuda/cuda_blas.cc:1452] Unable to register c

Predicting: |          | 0/? [00:00<?, ?it/s]

GPU available: True (cuda), used: True
TPU available: False, using: 0 TPU cores
HPU available: False, using: 0 HPUs


Predicting: |          | 0/? [00:00<?, ?it/s]

GPU available: True (cuda), used: True
TPU available: False, using: 0 TPU cores
HPU available: False, using: 0 HPUs


Predicting: |          | 0/? [00:00<?, ?it/s]

In [5]:
Y_hat_df.head()

unique_id                  ds  AutoNHITS   AutoTFT  AutoLSTM
0        OT 2018-02-21 00:00:00  -1.676568 -1.796490 -1.627110
1        OT 2018-02-21 01:00:00  -1.624879 -1.795265 -1.648109
2        OT 2018-02-21 02:00:00  -1.596442 -1.794987 -1.670991
3        OT 2018-02-21 03:00:00  -1.534124 -1.794949 -1.680664
4        OT 2018-02-21 04:00:00  -1.549119 -1.794943 -1.676927

In [12]:
Y_df

ds   index unique_id         y
0      2016-07-01 00:00:00       0      HUFL -0.279827
1      2016-07-01 01:00:00       1      HUFL -0.301290
2      2016-07-01 02:00:00       2      HUFL -0.387142
3      2016-07-01 03:00:00       3      HUFL -0.397873
4      2016-07-01 04:00:00       4      HUFL -0.354948
...                    ...     ...       ...       ...
100795 2018-02-20 19:00:00  118915        OT -2.003877
100796 2018-02-20 20:00:00  118916        OT -2.003877
100797 2018-02-20 21:00:00  118917        OT -1.776565
100798 2018-02-20 22:00:00  118918        OT -1.742809
100799 2018-02-20 23:00:00  118919        OT -1.726051

[100800 rows x 4 columns]

In [33]:
from utilsforecast.plotting import plot_series

plot_series(Y_df[Y_df["unique_id"] == target], Y_hat_df, engine="plotly")

In [23]:
cv_df = nf.cross_validation(df, n_windows=10, step_size=100)

GPU available: True (cuda), used: True
TPU available: False, using: 0 TPU cores
HPU available: False, using: 0 HPUs


Sanity Checking: |          | 0/? [00:00<?, ?it/s]

Training: |          | 0/? [00:00<?, ?it/s]

Validation: |          | 0/? [00:00<?, ?it/s]

Validation: |          | 0/? [00:00<?, ?it/s]

...

Validation: |          | 0/? [00:00<?, ?it/s]

Validation: |          | 0/? [00:00<?, ?it/s]

Validation: |          | 0/? [00:00<?, ?it/s]

`Trainer.fit` stopped: `max_steps=1000` reached.
GPU available: True (cuda), used: True
TPU available: False, using: 0 TPU cores
HPU available: False, using: 0 HPUs


Predicting: |          | 0/? [00:00<?, ?it/s]

In [24]:
cv_df.columns = cv_df.columns.str.replace('-median', '')
cv_df

unique_id                  ds              cutoff  AutoNHITS   AutoTFT  \
0          OT 2018-01-14 00:00:00 2018-01-13 23:00:00  -1.746711 -1.695189   
1          OT 2018-01-14 01:00:00 2018-01-13 23:00:00  -1.669354 -1.697763   
2          OT 2018-01-14 02:00:00 2018-01-13 23:00:00  -1.703740 -1.698393   
3          OT 2018-01-14 03:00:00 2018-01-13 23:00:00  -1.649806 -1.698485   
4          OT 2018-01-14 04:00:00 2018-01-13 23:00:00  -1.654967 -1.698497   
..        ...                 ...                 ...        ...       ...   
115        OT 2018-02-20 19:00:00 2018-02-20 11:00:00  -1.930711 -1.856766   
116        OT 2018-02-20 20:00:00 2018-02-20 11:00:00  -1.942013 -1.856766   
117        OT 2018-02-20 21:00:00 2018-02-20 11:00:00  -1.796414 -1.856766   
118        OT 2018-02-20 22:00:00 2018-02-20 11:00:00  -1.782183 -1.856766   
119        OT 2018-02-20 23:00:00 2018-02-20 11:00:00  -1.756610 -1.856766   

     AutoLSTM         y  
0   -1.740271 -1.759687  
1   -1.750031 -1.650161  
2   -1.761253 -1.692295  
3   -1.757639 -1.624904  
4   -1.771592 -1.633402  
..        ...       ...  
115 -1.644123 -2.003877  
116 -1.606921 -2.003877  
117 -1.583832 -1.776565  
118 -1.598030 -1.742809  
119 -1.619456 -1.726051  

[120 rows x 7 columns]

In [37]:
cutoff_index=6
total_cutoffs = len(cv_df["cutoff"].unique())
cutoff_value = cv_df["cutoff"].unique()[cutoff_index]
cutoff_time_index = df.index[df["ds"] == cutoff_value].tolist()
if len(cutoff_time_index) > 1:
    raise Exception(f"Unexpected cutoff_time_index length value: {len(cutoff_time_index)}. It should be always 1.")

cutoff_time_index = cutoff_time_index[0]
lookback = 120
horizon = 12
plot_series(
    df[cutoff_time_index-120:cutoff_time_index+12+1],
    cv_df[cv_df["cutoff"] == cv_df["cutoff"].unique()[cutoff_index]].drop(columns=['cutoff', 'y']),
    # cv_df.drop(columns="cutoff"),
    # max_insample_length= 12 * 10,
    ids=['OT'],
    engine="plotly"
)

In [40]:
from utilsforecast.evaluation import evaluate
from utilsforecast.losses import mse, mae, rmse, mape

In [41]:
evaluation_df = evaluate(cv_df.drop(columns='cutoff'), metrics=[mse, mae, rmse, mape])
evaluation_df['best_model'] = evaluation_df.drop(columns=['metric', 'unique_id']).idxmin(axis=1)
evaluation_df.head()

unique_id metric  AutoNHITS   AutoTFT  AutoLSTM best_model
0        OT    mse   0.009254  0.016726  0.029605  AutoNHITS
1        OT    mae   0.070591  0.105378  0.133690  AutoNHITS
2        OT   rmse   0.096195  0.129329  0.172061  AutoNHITS
3        OT   mape   0.044032  0.064842  0.080597  AutoNHITS

In [28]:
summary_df = evaluation_df.groupby(['metric', 'best_model']).size().sort_values().to_frame()
summary_df = summary_df.reset_index()
summary_df.columns = ['metric', 'model', 'nr. of unique_ids']
summary_df

metric      model  nr. of unique_ids
0    mae  AutoNHITS                  1
1    mse  AutoNHITS                  1
2   rmse  AutoNHITS                  1